(returns)=

# Returnanalyse 



```note
1. Returns und Renditen und deren statistische Auswertung
2. Portfoliowerte und Portfoliorenditen 

to do: 
* siehe Beispiel-Code: finance-pandas.ipynb
* Wiederholung wichtiger Pandas Grundlagen: Index als Datum anstalt Spalte und Umwandlung, sowie von Pandas vorgegebene Funktionen wie `plot()` oder `pct_change()` usw.) und als Übungsaufgabe -- erledigt
* mit aktuellen Datensatz mit einigen DAX-Aktien von oben / csv  -- erledigt
* Renditen vs. Returns -- Berechnung mit Hilfsfunktionen vs. eigene Berechnungen -- erledigt
* Portfoliowert und Rendite -- in Arbeit
* Berechnung empirischer Kennzahlen: mean, var, std, skewness, kurtosis... -- für Returns erledigt
* Portfoliovarianz
* einfache Grafiken: Zeitreihen, Hist, Scatterplots ... -- erledigt
* statistische Tests auf Normalverteilung... -- to do!!!
* Kovarianzmatrix / Korrelationsmatrix für Zusammenhang -- erledigt
* evt. in Anhang aufnehmen Grundlagen statistisches Testen und Arbeiten mit verschiedenen Verteilungen??? sowie multivariate Normalverteilung???
```


Zur Einschätzung der Entwicklung von Portfolien oder Aktienkursen betrachtet man nicht die Aktienkurse selbst, sondern deren Renditen bzw. Returns. Hierzu gibt es verschiedene Definitionen, die teilweise nicht einheitlich verwendet werden. Daher wollen wir Beginn die verschiedenen Renditedefinitionen nochmals aufgreifen. Zunächst betrachten wir nur einzelne Werte, egal ob Aktien oder andere Finanzprodukte und bezeichnen den Kurs zum Zeitpunkt $t$ mit $S_t$ und uns interessiert die Wertentwicklung der Aktie vom Anfangszeitpunkt $a$ nach $t$.

## Rendite vs. Log-Returns

👉 **Renditen** beschreiben den prozentualer Wertzuwachs von $a$ nach $t$: 
 
 $$
 R_{a,t} = \frac{S_{t} - S_{a}}{S_a}= \frac{S_t}{S_a}-1 
 $$

und werden auch als diskrete oder arithmetische Returns bezeichnet.
In der Finanzmathematik arbeitet man hingegen häufig mit den **Log-Returns**: 

$$
r_{a,t} = \log{\left( \frac{S_t}{S_a} \right)} = 
  \log {\left(S_t \right)} - \log {\left(S_a \right)},
$$

die teilweise auch als stetige oder geometrische Returns bezeichnet werden 
Wir werden gleich an einem realen Beispiel sehen, dass sich beide Renditebegriffe nur minimal unterscheiden, wobei mit 

$$
R_{a,t}=e^{r_{a,t}}-1 \Leftrightarrow r_{a,t} = \log{\left( R_{a,t}+1\right)}
$$ (rendite-vs-log-returns)

beide einfach ineinander umgerechnet werden können.

Das folgende Beispiel zeigt die Berechnung der täglichen Returns:

In [ ]:
import yfinance as yf
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
from datetime import datetime
import numpy as np

# Daten von Yahoo-Finance abrufen
ticker = "ALV.DE"
start_date = datetime(year = 2024, month=1, day = 1)


print("Versuche Yahoo Finance für %s:\n" % (ticker))
try:
    data = yf.download(ticker, start = start_date, group_by='ticker')
except Exception as e:
    print("Fehler bei Yahoo Daten Download: %s \n" % (e))

if not data.empty:
    data
    print(data.head())
    print(data.tail())
else: 
    print("Probleme bey yfiancne Download von %s" % ticker)

In [ ]:
df = data["ALV.DE"]
#Datum aus Index in Spalte holen: 
#   nur zur Demonstration, ist hier nicht von Belang ob Date als Index oder Spalte!
df = df.reset_index()
df2 = df[["Date", "Close"]].copy()
print(df2.head())

Verschiedene Methoden zur Berechnung beider Renditen:

In [ ]:
df2["Rendite"] = df2["Close"].pct_change()
df2['LogReturn'] = np.log(df2['Close']).diff()   # = log(C_t) - log(C_{t-1})
#nur zum Vergleich alternative Berechnungsformeln, die natürlich identische Werte liefern!
df2['Rendite2'] = df2['Close'] / df2['Close'].shift(1) - 1 
df2["LogReturn2"] = np.log(df2["Close"] / df2["Close"].shift(1))
df2["LogReturn3"] = np.log(df2['Rendite2'] +1)
print(df2.head())


Offensichtlich sind die Spalten Rendite und Rendite2 sowie die drei verschieden berechneten Log-Returns gleich. Mittels `plot()` können wir den zeitlichen Verlauf darstellen. Da die Schlusskurse und die Renditen völlig verschiedene Wertebereiche haben, ist ein simpler Plot aller Zeitreihen nicht sinnvoll, so dass wir zuvor noch die Schluss-Kurse entfernen. Probieren Sie zum Vergleich einfach mal den folgenden Befehl:

In [ ]:
df2.plot()

In [ ]:
#Entfernen der Closing-Kurse
df3 = df2.drop(columns="Close").dropna().copy()
#Durch Indexierung des Datums steht dieses autoamtisch auf der x-Achse, sonst der Integer-Index 0,1,2,..
df3 = df3.set_index("Date")

#plot aller Renditen
print(df3.head())
df3.plot(ylim=(-0.05,0.05))


**Hinweis**: die Pandas Methode `pct_change()` kann auch auf den kompletten DataFrame angewendet werden, solange das Datum als Index gesetzt ist. Dann werden die prozentualen Veränderungen auch für die Open, High und Low-Kurse berechnet. Ist das Datum allerdings als Spalte gesetzt, so führt der Aufruf zu einer Fehlermeldung, da die Funktion `pct_change()` nicht auf das Dates-Format angewendet werden kann. Außerdem werden die normalen Kurse überschrieben -- möchte man beispielsweise die Closing-Kurse im DataFrame erhalten, sollte wie oben in df2 einfach eine neue Variable / Spalte erzeugt werden.
**Hinweis**: Für die Berechnung der Renditen mittels der Pandas Funktion `pct_change()` ist es notwendig entweder eine konkrete Variable (Spalte) das DataFrames anzugeben, so wie das oben realisiert wurde. Ruft man mehrere Ticker gleichzeitig ab und möchte dann beispielsweise die Renditen auch gleichzeitig für alle Kurse berechnen, kann man andernfalls die Funktion `pct_change()` auch auf den gesamten DateFrame anwenden. Dann sollte man allerdings darauf achten, dass das Datum als Index gesetzt[^1] ist. Natürlich ist es auch möglich, die Funktion nur auf eine Teilmenge aller Spalten bzw. Variablen anzuwenden. 

[^1]: Die Indexierung des Datums kann einfach mittels Aufruf der Funktion `dataframe.set_index('Date')` gesetzt werden.



In [ ]:
data_all = data.pct_change()
data_all.head()

Obiger Graph der verschieden berechneten Renditen zeigt, dass auch zwischen der klassichen Rendite als prozentuale Veränderung und den Log-Returns keine großartigen Unterschiede mit bloßen Auge erkennbar sind, denn für sehr kleine Zeitabstände (hier 1 Tag) ist der Quotient $\frac{S_t}{S_{t-1}} \approx 1$ und somit die Unterschiede zwischen Log-Returns und Renditen nur marginal, was sich mit der Taylorapproximation 1. Ordnung der Funktion $f(x) = \log(x) \approx x-1 $ für $x$ nahe 1 erklären lässt. Berücksichtigt man höhere Ordnungen der Taylorapproximation $f(x) = \log(x) = x-1 - \frac 12 (x-1)^2 + \frac13 (x-1)^3 - \frac 14 (x-1)^4 \pm \ldots$ wird deutlich, warum sich aber insbesondere für $x\neq 1$ beide Return-Begriffe unterscheiden. 

In [ ]:
# x-Werte
x = np.linspace(0.01, 2, 400)     # für f(x) = ln(x), nur positive x

# Funktionen
f = np.log(x)
t = x - 1  #Taylor-Approximation 1. Oridnung

# Plot
plt.figure(figsize=(7,5))
plt.plot(x, f, label="f(x) = ln(x)", color="blue")
plt.plot(x, t, label="t(x) = x - 1", color="red")

# Achsen und Details
plt.axhline(0, color="black", linewidth=0.8)   # x-Achse
plt.axvline(0, color="black", linewidth=0.8)   # y-Achse
plt.title("f(x) = ln(x) und Taylorapproximation t(x) = x - 1")
plt.xlabel("x")
plt.ylabel("y")
plt.ylim([-2,1])
plt.legend()
plt.grid(True)
plt.show()


Es ist deutlich zu erkennen, dass für x nahe 1 kaum ein Unterschied zwischen beiden Funktionen zu erkennen ist. Zusammenfassend: Log-Returns und arithmetische Renditen unterscheiden sich für Tageskurse wegen $x= \frac{S_t}{S_{t-1}} \approx 1$

$$
r_{t-1,t} = \log{\left( \frac{S_t}{S_{t-1}} \right)} \approx \frac{S_t}{S_{t-1}} - 1 = R_{t-1,t} 
$$

nur minimal, da die Kursänderungen von Tag zu Tag nicht wesentlich sind. Beide Rendite-Begriffe haben aus finanzmathematischer Sicht Vor- und Nachteile, die wir später nochmals kurz aufgreifen werden. Aus praktischer Sicht macht  es hingegen kaum einen Unterschied, ob wir Renditen oder Log-Returns analysieren. Betrachtet man beispielsweise das Histogramm der täglichen Returns ist optisch kein wesentlicher Unterschied zwischen Log-Returns und Renditen erkennbar. Für Tagesrenditen bzw. -Returns schreibt man häufig $R_t$ bzw. $r_t$, d. h. lässt den ersten Zeitindex des Anfangsstadiums einfach weg. Außerdem zeigt die Graphik, dass die rote Kurve, welche den prozentualen Zuwächsen und somit Renditen entspricht, immer oberhalb der blaue Kurve verläuft, welche die Log-Returns beschreibt.

## Wertzuwachs über die Zeit: kumulierte Returns vs. Renditen

Die Log-Returns des Zuwachses von der Anfangsinvestition bis zum Zeitpunkt $t$ ist wegen 


\begin{align*}
r_{0,t} &= \log(S_t) - \log(S_0) = \log(S_t) - \log(S_{t-1}) + \log(S_{t-1}) \pm \ldots + \log(S_1)-\log(S_0)\\
&=r_{t-1,t} + \ldots + r_{0,1}
\end{align*}


gerade die Summe der täglichen Log-Returns. Somit folgt dann für die Renditen eine Produkt-Struktur


\begin{align*}
R_{0,t}+1 = \frac{S_t}{S_0}=e^{r_0,t}=e^{\sum\limits_{k=1}^t r_{k-1,k}} = \prod\limits_{k=1}^t e^{r_{k-1,k}} = \prod\limits_{k=1}^t \left(R_{k-1,k} +1 \right)
\end{align*}

also ähnlich wie beim (geometrischen) Verzinsen mit Zinseszinseffekten. 

Zusammenfassend werden wir die kumulierten Tages-Returns von 0 bis zum Zeitpunkt t zur Annualisierung verwenden

$$
r_{0,t} = \sum\limits_{k=1}^t  r_{k-1,k} 
$$(eq-logret-kum)

bzw.

$$
R_{0,t} = \prod\limits_{k=1}^t \left(R_{k-1,k} +1 \right) - 1 = e^{r_{0,t}} - 1
$$(eq-rend-kum)

Die Funktionen `cumsum()` und `cumprod()` berechnen für jede Spalte die kumulierten Summen bzw. Produkte, d. h. in der ersten Zeile wird die nur das erste Element und in der zweiten Zeile die ersten beiden Werte usw. in die Summe bzw. das Produkt berücksichtigt. Somit kann die Entwicklung über die Zeit beginnend vom Startwert für beide Returnarten einach berechnet werden.

In [ ]:
df3['LogReturns_kum']=df3['LogReturn'].cumsum()
df3['Rendite_kum']=(1+df3['Rendite']).cumprod()-1

print(df3.tail())

df3.LogReturns_kum.plot()
df3.Rendite_kum.plot()
plt.legend(['LogReturns','Rendite'])

Es ist deutlich zu erkennen, dass für die frühen Zeitpunkte $t$ sich die Log-Returns und Renditen von 0 (also Jahresanfang 2024) bis $t$ kaum unterscheiden. Mit steigender Zeit $t$ laufen die beiden Renditekurven allerdings auseinander, da sich für größere Zeitabstände eben beide Returndefinitionen unterscheiden. Wie erwartet liegen die (kumulierten) Renditen immer oberhalb der Log-Returns



(annulized-ret)=
## Annualisierte Returns  
<!--(evtl. erst nach Kovarianz verschieben!!! oder reicht Kommentar nach Kovarianz-Abschnitt) -->

Aus Gleichung {eq}`eq-rend-kum` folgt

$$
R_{0,t} = \prod\limits_{k=1}^t \left(R_{k-1,k} +1 \right) - 1 = y_\text{geo}^t - 1
$$ (eq-rend-geom-mean)

d. h. die kumulierte Rendite von 0 nach t lässt sich basierend auf der modifizierten Stichprobe der Tages-Renditen $y_k = R_{k-1,k}+1$ mit Hilfe des geometrischen Mittels für $n=t$

$$
y_\text{geo} = \sqrt[n]{\prod\limits_{k=1}^n y_k} = \left(\prod\limits_{k=1}^n y_k \right)^\frac 1n = \exp{\left( \frac 1n \sum\limits_{k=1}^n \log{y_k} \right)} = \exp{ \left(\overline{\log{y}}\right)}
$$ 

aller Tagesrenditen bis zum Zeitpunkt t ausdrücken. Ebenso können wir für die Log-Returns für die Stichprobe der Tages-Returns $x_k = r_{k-1,k}$ mittels des arithmetischen Mittels $\bar{x}=\frac 1n \sum\limits_{k=1}^n x_k$ wegen Formel {eq}`eq-logret-kum`  schreiben als

$$
r_{0,t} = \sum\limits_{k=1}^t r_{k-1,k} = t \bar{x} 
$$

Außerdem gilt folgender Zusammenhang zwischen geometrischen Mittel der Renditen und arithmetischen Mittel der Log-Returns für beliebige Stichprobengröße $n$

\begin{align*}
(R+1)_\text{geo} &= y_\text{geo} = \left(\prod\limits_{k=1}^n y_k \right)^\frac 1n = \exp{\left( \frac 1n \sum\limits_{k=1}^n \log{y_k} \right)}  = \exp{\left( \frac 1n \sum\limits_{k=1}^n \log{ \left( R_{k-1,k} + 1\right)} \right)} \\
&= \exp{\left( \frac 1n \sum\limits_{k=1}^n r_{k-1,k}  \right)} = \exp{\left( \frac 1n \sum\limits_{k=1}^n x_k  \right)} = \exp{\left( \overline x \right)} =
\exp{\left( \overline r \right)}
\end{align*}

Somit wird aus allen vorhanden Tages-Returns das jeweilige arithmetische und geometrische Mittel geschätzt und dann annualisiert man diese Werte entsprechend obiger Formeln, wobei man typischerweise unterstellt, dass ein Handelsjahr 252 Handelstage hat

$$
r_\text{annualized} = \bar{r}_\text{daily} \cdot 252
$$ (eq:log-annualized)

sowie 


\begin{align*}%eq-rendite-annualized
R_\text{annualized} &= (1 + R)_\text{geo,daily}^{252} - 1 = \exp{(r_\text{annualized})} - 1\\
& = \exp{\left(  \bar{r}_\text{daily} \cdot 252 \right)} - 1 % \approx \bar{r}_\text{daily} \cdot 252 \approx \bar{R}_\text{daily} \cdot 252
 \end{align*}


Insbesondere für statistische Analylsen werden häufig die Maßzahlen für jährliche Renditen angegeben, um eine bessere Vergleichbarkeit zwischen verschiedenen Anlageprodukten und Anlagezeiträumen durch die entsprechende Skalierung zu erreichen. 




In Abschnitt {ref}`portfolio-momente` benötigen wir die Erwartungswerte, Varianzen sowie Kovarianzen zwischen den einzelnen Aktienrenditen, um die erwartete Portfoliorendite und -Varianz zu berechnen. Für die Log-Returns ist dies aufgrund der Linearität des Erwartungswertes sehr einfach. Aus diesem Grund arbeitet man in der Finanzmathematik auch häufig lieber mit den Log-Returns als den Renditen. Unterstellt man, dass die Tages-Returns der $j$-ten Aktie $r_{j,(k-1,k)}$ unabhängig und identisch verteilte Zufallsvariablen (iid) mit $\mathbb{E} r_{j,(k-1,k)} = \mu_i$ und $\operatorname{Var} r_{j,(k-1,k)}=\sigma^2_j$ sind, folgt für die erwarteten Jahres-Log-Returns sowie deren Varianzen bzw. Volatilitäten / Standardabweichungen

$$
\mathbb{E} r_{j, \text {annualized}} = 252 \mu_j  = 252 \cdot \mathbb{E}  r_{j,\text{daily}}
$$(eq-expectation-year-log-return)

$$ 
\operatorname{Var}(r_{j,\text {annualized}}) = 252 \sigma^2_j = 252 \cdot \operatorname{Var}(r_{j,\text {daily}})
$$(eq-var-year-log-return)

$$
\operatorname{SD}(r_{j,\text {annualized}}) = \sqrt{252} \sigma_j
$$(eq-sd-year-log-return)

Zur Annualisierung der Kovarianz der täglichen Log-Returns führen wir folgende Bezeichnung ein: $X_k$ sei der zufällige Tages-Return der $i$-ten Aktie von Tag $(k-1)$-ten Tag zum $k$-ten Tag und für die $j$-te Aktie sei $Y_l$ der Tages-Return vom $(l-1)$-ten Tag zum $l$-ten Tag, d. h.

\begin{align*}
X_k &:= r_{i,(k-1,k)} := \log {\left( \frac{S_{i,k}}{S_{i,k-1}} \right)} =  \log S_{i,k} - \log S_{i,k-1}\\
Y_l &:= r_{j,(l-1,l)} := \log {\left( \frac{S_{j,l}}{S_{j,l-1}} \right)} =  \log S_{j,l} - \log S_{j,l-1}\\
\end{align*}

Mit {eq}`eq-logret-kum` folgt daher für die Jahres-Returns (für $t=252$)

\begin{align*}
r_{i,(0,t)} &= \log {\left( \frac{S_{i,t}}{S_{i,0}} \right)} = \sum\limits_{k=1}^t X_k\\
r_{j,(0,t)} &= \log {\left( \frac{S_{j,t}}{S_{j,0}} \right)} = \sum\limits_{l=1}^t Y_l\\
\end{align*}

Unterstellen wir zusätzlich zur Standardannahme (tägliche Returns einer Aktie sind identisch und unabhängig verteilt, d.h. $X_1, \ldots, X_t$ iid sowie $Y_1, \ldots, Y_t$ iid), dass ausschließlich die Tages-Returns zweier verschiedener Aktien am selben Tag korrelieren, also genauer 

$$
\operatorname{Cov}(X_k,Y_l) = \operatorname{Cov}(r_{i,(k-1,k)},r_{j,(l-1,l)})
= \begin{cases}
0, & \text{ falls  } k \neq l\\
\sigma_{ij}, & \text{ falls  } k = l
\end{cases}
$$

erhalten wir für die Kovarianz der Jahres-Returns zwischen der $i$-ten und $j$-ten Aktie wegen

\begin{align*}
\operatorname{Cov}(r_{i,(0,t)} ,r_{j,(0,t)} ) &=  \operatorname{Cov} \left(\sum\limits_{k=1}^t X_k, \sum\limits_{l=1}^t Y_l\right) = 
\sum\limits_{k=1}^t \sum\limits_{l=1}^t \operatorname{Cov}(X_k,Y_l)\\
&= \sum\limits_{k=1}^t \operatorname{Cov}(r_{i,(k-1,k)},r_{j,(k-1,k)}) = t \sigma_{ij},
\end{align*}

dass die Kovarianzen der Returns von 0 bis t einfach mit der Zeit skalieren

$$
\operatorname{Cov}(r_{i,(0,t)} ,r_{j,(0,t)} ) = t \sigma_{ij}
$$(eq-Kov-skal-Returns)

und somit die annualisierte Kovarianzmatrix aller Returns unter der Annahme dass ein Jahr 252 Handelstage besitzt

$$
\Sigma_\text {annualized} = 252 \cdot \Sigma_\text{daily},
$$(eq-Kov-Jahres-Returns)

wobei $\Sigma_\text{daily}$ die Kovarianzmatrix der Tages-Returns bezeichnet. 







Die Annualisierung für die prozentualen Zuwächse ist wegen der Nichtlinearität in {eq}`eq-rend-geom-mean` bzw. {eq}`eq-logret-kum` komplizierter, aber unter den obigen Annahmen der Unabhängigkeit der Tages-Renditen verschiedener Tage faktorisiert der Erwartungswert des Produktes. Analog zu den Log-Returns führen wir für die zufälligen Renditen folgende Bezeichnungen ein 

\begin{align*}
\tilde{X}_k &:= R_{i,(k-1,k)} + 1 = \frac{S_{i,k}}{S_{i,k-1}} \\
\tilde{Y}_l &:= R_{j,(l-1,l)} +1  = \frac{S_{j,l}}{S_{j,l-1}},
\end{align*}

wobei analog zu den Log-Returns $\mathbb{E} R_{i,(k-1,k)} = \tilde{\mu}_i$ und $\operatorname{Var} R_{i,(k-1,k)} = \tilde{\sigma}^2_i$ sowie 

$$
\operatorname{Cov}(\tilde{X}_k,\tilde{Y}_l) = \operatorname{Cov}(R_{i,(k-1,k)}+1,R_{j,(l-1,l)}+1) = \operatorname{Cov}(R_{i,(k-1,k)},R_{j,(l-1,l)})
= \begin{cases}
0, & \text{ falls  } k \neq l\\
\tilde{\sigma}_{ij}, & \text{ falls  } k = l
\end{cases}
$$

Aus Formel {eq}`eq-rend-kum` bzw. {eq}`eq-rend-geom-mean` folgt dann für die erwartete Jahres-Rendite 

\begin{align*} 
\mathbb{E} R_{i,(0,t)} &= \mathbb{E} \left( \prod\limits_{k=1}^t \left(R_{i,(k-1,k)} +1 \right)  - 1 \right)\\
&= \prod\limits_{k=1}^t \left( \mathbb{E}R_{i,(k-1,k)} +1 \right) -1 \\
&= \left( \prod\limits_{k=1}^t \left(\mathbb{E}  \tilde{X}_k \right)  - 1 \right) = \prod\limits_{k=1}^t \left( \tilde{\mu}_i + 1 \right) -1 = (\tilde{\mu}_i+1)^t - 1\\
\end{align*}

zusammengefasst also

$$
\mathbb{E} R_{i,(0,t)} = \prod\limits_{k=1}^t \left( \tilde{\mu}_i + 1 \right) -1 = (\tilde{\mu}_i+1)^t - 1
$$(eq-expectation-year-rendite)

und die Varianz skaliert wegen

\begin{align*} 
\operatorname{Var}(R_{i,(0,t)}) &= \operatorname{Var}\left( \prod\limits_{k=1}^t \tilde{X}_k -1 \right)  = \operatorname{Var}\left( \prod\limits_{k=1}^t \tilde{X}_k \right)\\
&= \mathbb{E}\left( \prod\limits_{k=1}^t \tilde{X}_k \right)^2 - \left(\mathbb{E} \left( \prod\limits_{k=1}^t \tilde{X_k} \right) \right)^2 \\
&=\mathbb{E}\left( \prod\limits_{k=1}^t \tilde{X}_k^2 \right) - \prod\limits_{k=1}^t \left( \mathbb{E} \tilde{X}_k \right)^2\\
&= \left( \tilde{\mu}_i^2 + \tilde{\sigma}^2_i + 2 \tilde{\mu}_i + 1 \right)^t - (\tilde{\mu}_i+1)^{2t}
\end{align*}

aus den Tageswerten

$$
\operatorname{Var}(R_{i,(0,t)}) = \left( \tilde{\mu}_i^2 + \tilde{\sigma}^2_i + 2 \tilde{\mu}_i + 1 \right)^t - (\tilde{\mu}_i+1)^{2t}
$$(eq-var-year-rendite)

Insbesondere die Skalierung der Varianz für die annualisierten Renditen ist demnach also deutlich komplexer und insbesondere auch nichtlinear in der Zeit $t$. Für die Kovarianzen der Jahres-Renditen zwischen der $i$-ten und $j$-ten Aktie 
ergibt sich bei analogen Annahmen zu den Log-Returns 

$$
\operatorname{Cov}(R_{i,(0,t)} ,R_{j,(0,t)} )
= \left( \tilde{\sigma}_{ij} + \tilde{\mu_i}\tilde{\mu_j} + \tilde{\mu}_i + \tilde{\mu_j} + 1\right)^t  - (\tilde{\mu}_i+1)^t  (\tilde{\mu}_j+1)^t
$$(eq-Kov-Jahres-Rendite)

denn


\begin{align*} 
\operatorname{Cov}(R_{i,(0,t)} ,R_{j,(0,t)} ) &= \operatorname{Cov}(R_{i,(0,t)} +1,R_{j,(0,t)} +1 )\\
&=  \operatorname{Cov} \left(\prod\limits_{k=1}^t \tilde{X}_k, \prod\limits_{l=1}^t \tilde{Y}_l\right)\\ 
&= \mathbb{E} \left( \prod\limits_{k=1}^t \tilde{X}_k - \mathbb{E} \left( \prod\limits_{k=1}^t \tilde{X}_k \right)\right) 
\left( \prod\limits_{l=1}^t \tilde{Y}_l - \mathbb{E} \left( \prod\limits_{l=1}^t \tilde{Y}_l \right)\right)\\
&= \mathbb{E} \left( \prod\limits_{k=1}^t \tilde{X}_k  - \prod\limits_{k=1}^t \mathbb{E}\tilde{X}_k  \right) \left( \prod\limits_{l=1}^t \tilde{Y}_l  - \prod\limits_{l=1}^t \mathbb{E}\tilde{Y}_l \right)\\
&= \mathbb{E} \left( \prod\limits_{k=1}^t \tilde{X}_k  - (\tilde{\mu_i}+1)^t   \right) \left( \prod\limits_{l=1}^t \tilde{Y}_l  - (\tilde{\mu}_j+1)^t\right)\\
&= \mathbb{E} \left( \prod\limits_{k=1}^t \tilde{X}_k \prod\limits_{l=1}^t \tilde{Y}_l \right) -  (\tilde{\mu}_j+1)^t \mathbb{E} \left( \prod\limits_{k=1}^t \tilde{X}_k \right)\\
& \quad - (\tilde{\mu}_i+1)^t \mathbb{E} \left( \prod\limits_{l=1}^t \tilde{Y}_l \right) +  (\tilde{\mu}_i+1)^t  (\tilde{\mu}_j+1)^t\\
&= \mathbb{E} \left( \prod\limits_{k=1}^t \tilde{X}_k \tilde{Y}_k \right) - (\tilde{\mu}_i+1)^t  (\tilde{\mu}_j+1)^t \\
&= \prod\limits_{k=1}^t \mathbb{E} \left(  \tilde{X}_k \tilde{Y}_k \right) - (\tilde{\mu}_i+1)^t  (\tilde{\mu}_j+1)^t \\
&= \left( \tilde{\sigma}_{ij} + \tilde{\mu_i}\tilde{\mu_j} + \tilde{\mu}_i + \tilde{\mu_j} + 1\right)^t  - (\tilde{\mu}_i+1)^t  (\tilde{\mu}_j+1)^t
\end{align*}

wobei die letzte Gleichung aus 

\begin{align*}
\tilde{\sigma}_{ij} &= \operatorname{Cov}(R_{i,(k-1,k)}, R_{j,(k-1,k)}) = \operatorname{Cov}(R_{i,(k-1,k)}+1, R_{j,(k-1,k)}+1)\\
&=\operatorname{Cov}(\tilde{X}, \tilde{Y})= \mathbb{E} \left(\tilde X \tilde Y \right) - \mathbb{E} \tilde{X} \cdot \mathbb{E} \tilde{Y} 
= \mathbb{E} \left(\tilde X \tilde Y \right) - (\tilde{\mu}_i +1)(\tilde{\mu}_j +1)
\end{align*}

folgt. Prinzipiell können wir also aus mit Formel {eq}`eq-expectation-year-log-return` von den täglichen Erwartungswertvektor bzw. Kovarianzmatrix der Renditen übergehen zu den annualisierten Werten, allerdings nicht so einfach wie für die Log-Returns. 

<!--
Wegen

\begin{align*} %eq-rendite-annualized-approx
R_\text{annualized} &= \exp{(r_\text{annualized})} - 1 = \exp{(252 r_\text{daily})} - 1\\
& \approx 252 \cdot \bar{r}_\text{daily}\\ &\approx 252 \cdot \bar{R}_\text{daily} 
\end{align*}  

wird aber häufig als Approximation vereinfachent genutzt. Wir werden unten bei der Berechnung der Portfolio-Varianz die Fehler dieser Approximation sehen.
-->

## Statistische Analyse der Returns

Wie oben gesehen sind die Unterschiede zwischen **täglichen** Log-Returns und Renditen nicht wesentlich. So sehen die Histogrammen, die die Verteilung der täglichen Wertzuwächse wiedergeben sehr ähnlich aus, wie die folgenden beiden Graphiken zeigen. 
Der folgende Code erzeugt nicht nur ein klassisches Histogramm, sondern fügt noch den Standard-Kerndichteschätzer[^2], was man einfach als empirische Dichtefunktion interpretieren kann, sondern auch noch zum Vergleich die angepasste Normalverteilungsdichte[^3].

[^2]: Standardmäßig basiert der Kerndichteschätzer auf glockenförmig überlagerten Gaussfunktionen, es können allerdings auch andere Kernels zur Schätzung verwendet werden, hier soll darauf allerdings nicht weiter eingegangen werden. Beispielsweise liefert das  [Statsmodels-Package](https://www.statsmodels.org/dev/examples/notebooks/generated/kernel_density.html) verschiedene andere Kernels. 

[^3]: Die Parameter der Normalverteilung werden mittels der Funktion `fit()` vpm [Normalverteilungs-Sub-Package](https://docs.scipy.org/doc/scipy/reference/generated/scipy.stats.norm.html) geschätzt, können aber natürlich auch einfach mittels aritmetischen Mittel und empirischer Standardabweichung aus  dem Numpy-Package geschätzt werden.  

In [ ]:

from scipy.stats import norm

#Parameter der NV aus Daten schaetzen
mu_log, std_log = norm.fit (df3.LogReturn) 

#Alternative mit selben Schaetzwerten 
#mu2 = np.mean(df3['LogReturn'])
#std2 = np.std(df3['LogReturn'])
#print("Schätzer mu=%f vs mu2 =%f" % (mu, mean))
#print("Schätzer std=%f vs std2 =%f" % (std, std2))

# x Werte fuer Dichteplot der Normalverteilung
x = np.linspace(min(df3['LogReturn']), max(df3['LogReturn']), 1000)

#Histogramm mit kernel
sns.histplot(df3['LogReturn'], stat = 'density', kde=True)

#Dichte = pdf mit gefitteten Parametern
y = norm.pdf(x, mu_log, std_log)

#hinzufügen der Dichte zum Histogramm:
plt.plot(x, y, color='red')
#Legende hinzufügen
plt.legend(['Kerndichteschätzer','Normaldichte'])

In [ ]:
#Analoges Vorgehen für Renditen
mu, std = norm.fit (df3.Rendite) 
x = np.linspace(min(df3['Rendite']), max(df3['Rendite']), 1000)
sns.histplot(df3['Rendite'], stat = 'density', kde=True)
y = norm.pdf(x, mu, std)
plt.plot(x, y, color='red')
plt.legend(['Kerndichteschätzer','Normaldichte'])

Der Kerndichteschätzer zeigt eine typische glockenförmige Verteilung. Allerdings zeigt der Vergleich zwischen Kerndichteschätzer und Normalverteilungsdichte eine recht deutlichte Abweichung zur Normalverteilung. In den Rändern der empirischen Verteilung liegen deutlich mehr Werte als bei der Normalverteilung üblich. Insbesondere die linke Seite, die starke Verluste repräsentiert, ist stärker ausgeprägt und dies spricht für eine leptokurtsiche Verteilung. Mit Hilfe der 3. und 4. Momente werden wir dies auch mit Hilfe statistischer Maßzahlen in [](momente) ausdrücken.

In [ ]:
print("mittlere Tages-Rendite: %f Tages-LogReturns: %f" % (mu, mu_log))
print("Standardabweichung Tages-Rendite: %f Tages-LogReturns: %f" % (std, std_log))

Oben haben wir bereits mittleren Tages-Returns und die Standardabweichungen berechnet. Allerdings kann man dies auch gleich spaltenweise für den gesamten DataFrame. Zu beachten gilt hier natürlich, ob die Maßzahl tatsächlich auch sinnvoll für jede Variable / Spalte ist. Die Mittelung der durchschnittlich kumilierten Returns ist beipspielsweise nicht sinnvoll, da für jede Zeile verschiedene Zeitpunkte betrachtet werden und somit keine stationäre Zeitreihe mehr vorliegt. Daher sollten die letzten beiden Spalten bei der Interpretation ausgelassen (oder noch besser ausgeblendet) werden, wie wir im Folgenden noch demonstrieren.

In [ ]:
df3.mean()

In [ ]:
df3.std()

Die `describe()` Funktion liefert eine Übersicht der wichtigsten Statistik-Maßzahlen

In [ ]:
df3.describe()

Mittels `apply()` können auch einzelne oder mehrere Funktionen auf die Spalten (axis = 0) bzw. Zeilen (axis=1) angewendet werden

In [ ]:
df3.apply([np.mean, np.std], axis = 0)

Natürlich können auch eigene Funktionen angewendet werden. Der folgende Code zeigt beispielhaft die selbstständige Berechnung der ersten beiden empirischen Momente:

In [ ]:
def my_mean(x):
    return np.sum(x) / x.size

def my_var(x, correction = True):
    n = x.size
    m = my_mean(x)
    ss = ((x-m)**2).sum()
    df = n #biased variance estimator!
    if correction:
        #Bessel correction gives unbiased variance estimate
        df = df - 1
    return ss/df
    
def my_var2(x):
    n = x.size
    m = my_mean(x)
    ss = (x**2).sum() - n*m**2
    return ss/(n-1)

def my_var_biased(x):
    return my_var(x, correction=False)


def my_sd(x):
    return np.sqrt(my_var(x))    

df3.apply([my_mean, my_var, my_var_biased, my_sd], axis = 0, correction = True)


Die Berechnung der statistischen Kennzahlen für die kumulierten Returns (letzten beiden Spalten) macht wie oben bereits erwähnt keinen Sinn, daher schließen wir sie einfach aus der Auswertung aus. 

In [ ]:
df3.drop(columns=["LogReturns_kum","Rendite_kum"]).apply([my_mean, my_var, my_var_biased, my_sd], axis = 0, correction = True)

Alternativ kann man natürlich einfach die Variablen angeben, die man auswerten möchte: hier bietet sich neben der Funktion `drop()` auch die Pandas Funktion `filter()` an, bei der man beispielsweise mittels sogenannter <a href="https://docs.python.org/3/howto/regex.html" target="_blank" rel="noopener noreferrer">Regular Expressions</a> (siehe auch <a href="https://howtoregex.com/cheat-sheet/python" target="_blank" rel="noopener noreferrer">Regex Cheat Sheet</a>) sehr vielfältige Bedingungen formulieren kann, siehe
<a href="https://pandas.pydata.org/pandas-docs/stable/reference/api/pandas.DataFrame.filter.html" target="_blank" rel="noopener noreferrer">Pandas Docu</a>.
Im folgenden Code wollen wir alle Variablen die mit 'Log' beginnen (`^Log`) aber am Ende **nicht** auf '_kum' enden (negative lookahead: `(?!.*_kum$)`) auswerten:


In [ ]:
df3.filter(regex=r"^Log(?!.*_kum$)").apply([my_mean, my_var, my_var_biased, my_sd], axis = 0, correction = True)

**Hinweis**: man kann das beliebig individualisieren. In manchen Auswertungen möchte man beispielsweise nur Variablen mit numerischen Werten auswerten, dann ist die Funktion `select_dtypes()` für die Auswahl bestimmer Datentypen hilfreich.

Ebenso kann die Funktion `agg()` wie die Funktion `apply()` angewendet werden: 

In [ ]:
df3.drop(columns=["LogReturns_kum","Rendite_kum"]).agg([my_mean, np.mean, my_var, my_var2, my_var_biased, my_sd, np.std])


(momente)=
### höhere Momente: Schiefe und Kurtosis

Allgemein kann die Verteilung einer Stichprobe mittels der empirischen zentralen bzw. allgemeinen Momente 

$$
\tilde{M}_k = \frac 1n \sum\limits_{i=1}^n \left( x_i - \bar{x} \right)^k \qquad \text{ bzw. } \qquad M_k = \sum\limits_{i=1}^n x_i^k
$$

beschrieben werden. Während das 1. Moment $M_1 = \overline x$ den Mittelwert der Verteilung beschreibt, wird die Schwankung mittels des 2. Moments beschrieben und entspricht dem unkorrigierten Varianzschätzer 

$$
\tilde{M}_2 = \tilde{s}^2 = \frac 1n \sum\limits_{i=1}^n (x_i - \overline x)^2 = \frac 1n \sum\limits_{i=1}^n x_i^2 - \overline{x}^2 = M_2 - M_1^2
$$

Die sogenannte Z-Transformation einer Stichprobe $x_1, x_2, \ldots, x_n$ ist eine Standardisierung[^4] der Werte 
$z_i = \frac{x_i - M_1}{\sqrt{M_2}} = \frac{x_i - \overline x}{\tilde s}$, so dass diese Stichprobe wegen $M_1(z) = \frac1n \sum\limits_{i=1}^n z_i = 0$ um die Null schwankt mit Varianz 

\begin{align*}
\tilde{M}_2(z) &= \frac 1n \sum\limits_{i=1}^n (z_i - \overline{z})^2 = \frac 1n \sum\limits_{i=1}^n z_i^2 = 
\frac 1n \sum\limits_{i=1}^n  \left( \frac{x_i - \overline{x} }{\tilde s} \right) ^2\\
&= \frac{\frac 1n \sum\limits_{i=1}^n \left( x_i - \overline x \right)^2}{\tilde s^2} = \frac{\tilde{M}_2(x)}{\tilde{M}_2(x)}= 1
\end{align*}


In [ ]:
def my_central_moments(x,k):
    n = x.size
    m = x.sum()/n
    return ((x-m)**k).sum()/n

#2. Moment = Varianz
s2 = my_var(df3['LogReturn'])
s2_1 = my_central_moments(df3['LogReturn'], 2)
s2_2 = my_var_biased(df3['LogReturn'])

print("unbiased var = %f, 2. zentrales Moment = %f, biased var = %f" %  (s2,s2_1, s2_2))


[^4]: Arbeitet man mit höheren Momenten verwendet man zur Standardisierung aus Bequemlichkeit häufig den verzerrten Varianzschätzer $\tilde{s}^2 = \tilde{M}_2$ anstatt die korrigierte und somit erwartungstreue Version $s^2 = \frac{n}{n-1} \tilde{M}_2 = \frac1{n-1} \sum\limits_{i=1}^n (x_i - \overline{x})^2$. Bei einigen implementierten Funktionen kann durch ein zusätzliches Argument zwischen unverzerrten und verzerrten Schätzern gewählt werden. Hier sollte vor Verwendung immer die Dokumentation betrachtet werden.




Mittels dem 3. Moment wird die (empirische) **Schiefe** einer Verteilung berechnet

\begin{align*}
	g &= \frac{\tilde{M}_3(x)}{\tilde{M}_2(x)^\frac 32} = \frac{\frac{1}{n}\sum\limits_{i=1}^n \left( x_i - \bar{x} \right)^3}{\sqrt{ \left( \frac{1}{n}\sum\limits_{i=1}^n \left( x_i - \bar{x} \right)^2 \right)^3}} \\
    &= \frac{ 
     \left(\frac 1n \sum\limits_{i=1}^n (x_i - \bar{x}) \right)^3}{\tilde s^3} = \frac 1n
    \sum\limits_{i=1}^n \left( \frac{x_i - \overline x}{\tilde s} \right)^3 = \tilde{M}_3(z).
\end{align*}

Für symmetrische Verteilungen verschwindet die Schiefe  ($\bar{x} \approx x_{med} \approx x_{mod}$, $g \approx 0$), während für linksschiefe (rechtssteil) Verteilungen der Wert negativ wird  ($\bar{x} < x_{med} < x_{mod}$, $g<0$) und für rechtsschiefe (linkssteil) Verteilungen  ($\bar{x} > x_{med} > x_{mod}$, $g>0$) sich ein postiver Wert ergibt. 



In [ ]:
def schiefe(x):
    m = x.sum()
    s = np.sqrt(my_central_moments(x,2))

    #s = x.std(ddof=0)   # Populations-Std für Normierung
    #n = x.size
    z = (x-m)/s
    return (my_central_moments(z,3))

#3. Moment / Schiefe
m3 = my_central_moments(df3['LogReturn'], 3)
g = schiefe(df3['LogReturn'])

print("Schiefe: g = %f basierend auf 3. zentralen Moment = %f" %  (g, m3))

Mittels 4. Moment misst man die Wölbung bzw. Krümmung einer Verteilung

$$
\gamma = \frac{\tilde{M}_4(x)}{\tilde{M}_2^2(x)}-3 = \frac{\frac{1}{n}\sum\limits_{i=1}^n \left( x_i - \bar{x} \right)^4}{\left( \frac{1}{n}\sum\limits_{i=1}^n \left( x_i - \bar{x} \right)^2 \right)^2} - 3  = \frac 1n \sum\limits_{i=1}^n \left( \frac{x_i - \bar{x}}{\tilde s} \right)^4 -3 =  \tilde{M}_4(z) -3
$$

wobei die Verschiebung um 3 für die bessere Interpretierbarkeit bzw. dem Vergleich zur Normalverteilung dient, denn diese Kennzahl vergleicht wie stark  der zentrale Bereich und folglich auch wie schwach die 'tails' im Vergleich zur Normalverteilung besetzt sind.
Werte von $\gamma \approx 0$ sind typisch für eine Normalverteilung, während positive Werte für eine spitzere Verteilung ($\gamma > 0$) mit mehr Maße in den Tails und negative Werte für eine breitere Verteilung ($\gamma < 0$) sprechen.
	

In [ ]:
def woelbung(x):
    m = x.sum()
    s = np.sqrt(my_central_moments(x,2))

    #s = x.std(ddof=0)   # Populations-Std für Normierung
    #n = x.size
    z = (x-m)/s
    return (my_central_moments(z,4) - 3)

#4. Moment / Krümmung
m4 = my_central_moments(df3['LogReturn'], 4)
k = woelbung(df3['LogReturn'])

print("Kurtosis: gamma = %f basierend auf 4. zentralen Moment = %f" %  (k, m4))


In [ ]:
df3.drop(columns=["LogReturns_kum","Rendite_kum"]).agg([schiefe, woelbung])


Natürlich gibt es auch enstprechende Pakete, um diese Kennzahlen einfach zu berechnen. Hier nutzen wir das Sub-Package `scipy.stats`


In [ ]:
from scipy.stats import skew, kurtosis, moment

#g = schiefe(df3['LogReturn'])
#k = woelbung(df3['LogReturn'])
#Package Version:
g2 = skew(df3['LogReturn'])
k2 = kurtosis(df3['LogReturn'])
m3_sci = moment(df3['LogReturn'],  order=3)

print("Schiefe: g = %f, scipy.stats.skew  = %f" %  (g, g2 ))
print("3. Moment: m3 = %f, scipy.stats.moment = %f" % (m3, m3_sci))

print("Kurtosis: k = %f, Scipy.stats.kurtosis  = %f" %  (k, k2))

#kompletter DataFrame
print("Skew: %s" % df3.skew())

print("Kurtosis: %s" % df3.kurtosis())




Wir haben hier ausschließlich Tages-Returns ausgewertet, allerdings haben wir in {ref}`annulized-ret` gesehen, wie wir diese zu Jahres-Returns skalieren können. Insbesondere Schiefe und Kurtosis sind im Gegensatz zu den zentrierten 3. bzw. 4. Momenten aber skalierungsfrei, da sich die Skalierungsfaktoren bei der Normierung herauskürzen. 

(testnormal)=
### Test auf Normalverteilung 

to do
* graphische Analyse mit Histogramm und qq-plots
* Shapiro Wilk, KS-Test, Liliefors Korrektur, usw.
* scipy: normaltest [](https://docs.scipy.org/doc/scipy/tutorial/stats/hypothesis_normaltest.html#hypothesis-normaltest)

In [ ]:
from scipy import stats
test1 = stats.shapiro(df3['LogReturn'])
print(test1)
test2 = stats.normaltest(df3['LogReturn'])
print(test2)

to do: Auswertung... alle p-values sehr klein (<0.05) und somit signifikanter Nachweis, dass Log-Returns nicht normalverteilt...



### Abhängigkeiten zwischen Aktien-Returns: Kovarianz und Korrelation

<!-- ## Zusammenhangsmaße: Kovarianz und Korrelation -->

Zur statistischen Auswertung zählt natürlich auch die Analyse der Abhängigkeiten zwischen verschiedenen Aktien. Im folgenden Abschnitt {ref}`portfolio` werden wir aus verschiedenen Aktien ein Portfolio zusammenstellen und desen Entwicklung näher untersuchen. Bevor wir Portfolio-Returns studieren, untersuchen wir noch die Abhängigkeiten zwischen den einzelnen Aktien-Returns. Der Übersichtlichkeit wählen wir hier 4 Aktien und laden deren Kurse bei YahooFinance herunter:

In [ ]:
tickers = ["AAPL", "MSFT", "GOOGL", "TSLA"]

# Kurse herunterladen (letztes Jahr)
portfolio_data = yf.download(tickers, period="5y")  
#print(data.head())

#wollen nur Schlusskurse untersuchen
close_df = portfolio_data["Close"].copy()

print(close_df.head())
close_df.plot()


Teilweise verlaufen alle 4 Kurse sehr ähnlich, teilweise aber auch individuell. Sinnvoll ist daher der Übergang zu den Renditen und die Analyse derer Abhängigkeiten. 

In [ ]:
renditen = close_df.pct_change()

print(renditen.head())
renditen.plot(alpha = 0.7)

Während oben bereits der zeitliche Verlauf unterschiedliche Zusammenhänge verdeutlicht, ist die Darstellung in Scatterplots übersichtlicher: 

In [ ]:
pd.plotting.scatter_matrix(renditen, figsize=(6, 6), diagonal="hist")
plt.show()

In [ ]:
sns.pairplot(renditen)
plt.show()

Natürlich können auch nur einzelne Paare beispielsweise mittels der Seaborn Funktionen `scatterplot()` oder `relplot()` dargestellt werden. Auf den ersten Blick unterscheiden sich die Funktionen nicht, allerdings liefert die zweite Funktionen flexiblere Anpassungsmöglichkeiten[^5].

[^5]: Die Funktion `relplot()` erzeugt sogenannte 'relational plots' und kann neben Scatter-Plots auch Line-Plots erzeugen und kann im Gegensatz zu `scatterplot()` mehrere Sub-Plots in einer Graphik darstellen. Für Details und Beispiele verweisen wir hier auf die [Seaborn-Doku](https://seaborn.pydata.org/generated/seaborn.relplot.html).

In [ ]:
sns.scatterplot(data = renditen, x='AAPL', y='TSLA')

In [ ]:
sns.relplot(data = renditen, x='AAPL', y='TSLA', kind = 'scatter')

Alle Scatter-Plots zeigen einen mehr oder weniger starken positiven Zusammenhang zwischen den Renditen zweier Aktien. Steigt die Rendite der einen Aktie, dann steigt üblicherweise auch die der anderen Aktie und fällt die eine Rendite, dann auch die andere. Die einfachste statistische Maßzahl zur Erfassung des Zusammenhangs sind die (empirische) Kovarianz und Korrelation[^6], die allerdings nur den linearen Zusammenhang erfassen.
Die (unverzerrte) empirische Kovarianz zweier Stichproben $(x,y)=((x_1,y_1), \ldots, (x_n,y_n))$ wird mittels

$$
s_{xy} = \frac1{n-1} \sum\limits_{i=1}^n (x_i - \overline x)(y_i - \overline y) = \frac 1{n-1} \left(\sum\limits_{i=1}^n x_i y_i - n  \overline x \overline y \right)
$$

berechnet. Die Korrelation entsteht durch Normierung und ist einfacher zu interpretieren

\begin{align*}
r_{xy} &= \frac{s_{xy}}{s_x \dot s_y} = \frac{\sum\limits_{i=1}^n (x_i - \overline x)(y_i - \overline y)}{\sqrt{\sum\limits_{i=1}^n (x_i - \overline x)^2 \cdot \sum\limits_{i=1}^n (y_i - \overline y)^2}}\\
&= \frac{\sum\limits_{i=1}^n x_i y_i - n  \overline x \overline y}{\sqrt{\left(\sum\limits_{i=1}^n x_i^2 - n  \overline x^2\right) \left(\sum\limits_{i=1}^n y_i^2 - n  \overline y^2 \right)}} \in [-1,1]
\end{align*}

[^6]: Die Kovarianz zweier Zufallsvariablen $X$ und $Y$ ist definiert als $\operatorname{cov}(X,Y) = \mathbb{E}(X-\mathbb{E})(Y-\mathbb{E}Y)=\mathbb{E}(XY)-\mathbb{E}X \cdot \mathbb{E}Y$ und die Korrelation nach Pearson  $\operatorname{cor}(X,Y) = \frac{\operatorname{cov}(X,Y)}{\sqrt{\operatorname{Var}(X) \cdot \operatorname{Var{Y}}}} \in [-1,1]$ skaliert die Werte für eine bessere Interpretierbarkeit. Aus Unabhängigkeit folgt wegen $\mathbb{E} XY = \mathbb{E} X \cdot \mathbb{E} Y$ gerade $\operatorname{cov}(X,Y)=0$ und somit Unkorreliertheit, die Rückrichtung gilt allerdings im Allgemeinen nicht, beispielsweise sind $X \sim \mathcal{N}(0,1)$ und $Y=X^2$ offensichtlich abhängig (quadratischer Zusammenhang), aber unkorrelierte Zufallsvariablen da $\operatorname{cov}(X,Y)= \mathbb{E}(XY)-\mathbb{E}X \cdot \mathbb{E}Y = \mathbb{E}(X^3) = 0$ gilt.
<!-- check \cov klappt nicht in _config.yml - warum??? -->

Pandas hat die Berechnung der empirischen Kovarianz- und Korrelation bereits implementiert und fasst alle paarweisen Kombinationen in der Kovarianz- bzw. Korrelationsmatrix zusammen. Auf der Diagonalen der Kovarianzmatrix stehen also die Varianzen.

In [ ]:
kov_matrix = renditen.cov()
print(kov_matrix)

In [ ]:
korr_matrix = renditen.corr()
print(korr_matrix)

Zum Abschluss zeichnen wir noch die Regressionsgerade in den Scatterplot ein, um den linearen Zusammenhang zu veranschaulichen. Mit Regressionsmodellen beschäftigen wir und noch ausführlich in Abschnitt {ref}`regression`

In [ ]:
sns.regplot(data=renditen, x="AAPL", y="MSFT",  ci = None)

👉Der Zusammenhang der täglichen Log-Returns ist völlig analog zu analysieren und sollte zu Übungszwecken selbstständig durchgeführt werden.

### to do: Vorsicht bei der Skalierung der 'zeitlineare' Log-Returns um von Tages-Returns zu Jahres-Returns überzugehen

* bisher: annualisiere Erwartungswert und Kovarianz aus Daily Maßzahlen 
* einfacher Vergleich der skalierten Log-Returns zeigt es ist falsch: annualisiere Returns durch Zeitskalierung und berechne Maßzahlen, Erwartungswerte sind identisch aber Kovarianz / Varianz wird maßlos überschätzt! Grund für iid Zufallsvariablen $X_1$ ist $X_1 + X_2 \neq 2 X_1$ denn Varianz ist deutlich höher!!!
* siehe Skript Alois re-skalierung!

Wir haben bei der Analyse der Tages-Returns gesehen, dass die Unterscheidung zwischen Log-Returns (zeitstetige Returns) und Renditen (arithmetische Returns, zweitdiskrete Returns) nur unwesentliche Unterschiede aufzeigen, da für Tages-Kurse beide Return-Begriffe zu verschiedenen, aber sehr ähnlichen Werten führen. Beide Definitionen haben entscheidente Vor- aber auch Nachteile. Die Log-Returns werden aufgrund ihrer kumulierenten Summeneigenschaft sowie der damit engen Verbindung mit der Normalverteilung (zentraler Grenzwertsatz) häufig für zeitstetige Modelle oder Modelle mit Normalverteilungsannahmen verwendet. Insbesondere ist der Übergang von täglichen zu jährlichen Returns im Gegensatz zu den Renditen sehr einfach.  Wir werden in Abschnitt {ref}`portfolio` noch sehen, dass sich die Portfoliorendite von der Anfangsinvestition zum Zeitpunkt 0 bis nach $t$ einfach als gewichtete Summe der Aktien-Renditen von $0$ bis $t$ berechnen lässt, was für Log-Returns nur näherungsweise gilt. Dennoch haben sich aber wegen der einfachereren Skalierbarkeit auch hier die Log-Returns gegenüber den Renditen durchgesetzt.


Werden allgemein die Aktienkurse zu den Zeitpunkten $t_0, t_1, \ldots, t_n$ gemessen, so kann man die annualisierten Log-Returns (siehe Vorlesungsskript <a href="https://www.tu-chemnitz.de/mathematik/fima/public/LecturesAndMaterials/PortfolioOptimierung.pdf" target="_blank">Portfoliooptimierung Prof. Pichler</a>) definieren als



\begin{align*}  %annu-log-return
\xi_i^j := \frac{1}{t_i - t_{i-1}} \log{\left( \frac{S_{j,t_i}}{S_{j,t_{i-1}}}\right)} = \frac{1}{t_i - t_{i-1}} r_{j,(t_{i-1},t_i)}
\end{align*}
 
Dann muss allerdings auch der Gesamt-Return von $t_0$ nach $t_n$ annualisiert werden


\begin{align*} %
\xi_{total} &:= \frac{1}{t_n - t_{0}} \log{\left( \frac{S_{t_n}}{S_{t_{0}}}\right)} = \frac{1}{t_n - t_{0}} r_{t_0,t_n}\\
&=  \frac{1}{t_n - t_{0}} \sum\limits_{i=1}^n r_{t_{i-1},t_i}
\end{align*}

Für äquividistante Tagesdaten wählt man $t_i = \frac{i}{252}$, so dass $t_{i}-t_{i-1} = \frac 1 {252}$, für Monatskurse $\frac{i}{12}$ erhält man entsprechend $t_i - t_{i-1} = \frac 1{12} $ und für Quartalsdaten $t_i=\frac{i}{4}$ entsprechend $t_i - t_{i-1} = \frac 1{4}$.
<!-- siehe portfolio-rendite-vs-log-return.py in Ordner Beispiel-Code -->



!!! to do: code überarbeiten bzw. verschieben!!!

In [ ]:
trading_days = 252

In [ ]:
log_returns = np.log(renditen + 1)
mu = log_returns.mean()

mu_tilde = renditen.mean()
geo_mean_renditen = np.exp((np.log(renditen+1)).mean()) - 1

print("mean daily R %s: \n " % mu_tilde)
print("geometric mean daily R %s: \n" % geo_mean_renditen)
print("check: geo mean Rendite = exp(mean daily log)-1 = %s \n" % (np.exp(mu)-1) )
print("Daily log-returns %s: \n" % mu)

In [ ]:
#annualization: from daily means to yearly means

mu_year = mu * trading_days

mu_tilde_year  = (mu_tilde+1) ** trading_days - 1

mu_tilde_year_approx1 = mu_tilde * trading_days 
mu_tilde_year_approx2 = np.exp(mu_year) -1
#mu_tilde_year_approx3 = mu_year


print("mu year (Log-Returns r) %s: \n " % mu_year)
print("mu_tilde year (Renditen R) %s: \n " % mu_tilde_year)
print("Approximation1 : mu_tilde_year = mu_tilde * trading days %s\n " % (mu_tilde_year_approx1))
print("Approximation2: exp(mu_year) -1  %s: \n" % (mu_tilde_year_approx2))


Wir sehen Abweichungen zwischen den geometrischen und arithmetischen Mittelwerten der täglichen Renditen bzw. Log-Returns. 
Außerdem sehen wir den den nichtlineare Zusammenhang zwischen mittleren Log-Returns und geometrischen Mittel der Renditen. Nun werden diese Mittel annualisiert. 

Nach obiger Formel -- TO DO!!!!!

<!--to do Alois  https://www.tu-chemnitz.de/mathematik/fima/public/LecturesAndMaterials/CAPM-Markowitz-plotly.html  -->

In [ ]:
from datetime import datetime

print(log_returns.head())
print(log_returns.tail())
annulalized_log_returns = log_returns.copy()

kalendertage = (annulalized_log_returns.index[-1] - annulalized_log_returns.index[0]).days

print("Tage insgesamt: %s, Jahre: %s" % (kalendertage, kalendertage / 365))

#annulalized_log_returns = annulalized_log_returns.reset_index()
for i in range(1,len(log_returns)):
    annulalized_log_returns.iloc[i] = annulalized_log_returns.iloc[i]* 365  / (annulalized_log_returns.index[i] - annulalized_log_returns.index[i-1]).days

print(annulalized_log_returns.head()    )
print(annulalized_log_returns.tail()    )

mu_annulalized_log_returns =  annulalized_log_returns.mean()

print(mu_annulalized_log_returns)



Kovarianzen annualisieren...remove-cell


In [ ]:
Sigma_day = log_returns.cov()
Sigma_year = Sigma_day * trading_days 

Sigma_tilde_day = renditen.cov()

#Dummy zur simultanen Berechnung von (mu_tilde_i + 1)(mu_tilde_j + 1)
mu_tilde_dummy = np.outer(mu_tilde + 1, mu_tilde + 1)
#print(mu_tilde_dummy)

Sigma_tilde_year = (Sigma_tilde_day + mu_tilde_dummy)**trading_days - mu_tilde_dummy**trading_days

Sigma_tilde_year_approx1 = Sigma_year
Sigma_tilde_year_approx2 = Sigma_tilde_day * trading_days


print("Annualized covarince R (percentege changes)")
print(Sigma_tilde_year)

print("Approx1: Annualized covarince R (percentege changes): Sigma \approx Sigma_tilde")
print(Sigma_tilde_year_approx1)

print("Approx2: Annualized covarince R (percentege changes): yearly cov = daily cov * 252")
print(Sigma_tilde_year_approx2)


print("Annualized covariance r (log retunrs)")
print(Sigma_year)


In [ ]:
log_returns_scaled = log_returns * trading_days
print(log_returns_scaled.mean())
print(mu_year)

print(log_returns_scaled.cov())
print(Sigma_year)

Fazit: wir sehen dass die Skalierung der Log-Returns zwar zum exakten Erwartungswert-Vektor führt, aber die Kovarianz deutlich überschätzt, denn $\mathrm{E} (X_1 + X_2 + \ldots + X_n ) = \mathrm{E} (nX_1)$, aber $var(nX_1)=n^2 Var(X_1) \neq n Var(X_1)= var(X1+\ldots+X_n)$ to do -- sauber formulieren!!!

(portfolio)=
## Portfolio-Returns 

Aus den obigen 4 Aktien stellen wir jetzt ein Portfolio zusammen und investieren 1000\$ zu 10% in 1. Aktie (AAPL), 30% in 2. Aktie (MSFT), 40% in 3. Aktie (GOOGL) und die verbleibenden 20% in 4.Aktie (TSLA) und schichten das Portfolio im Folgenden nicht mehr um. Die Gewichtung ist hier übrigens absolut willkürlich gewählt und kann beliebig geändert werden. Uns interessiert die Wertentwicklung des Portfolios und daher betrachten wir die Portfolio-Returns bzw. Renditen. 

**Achtung** wenn der Vektor mit den Aktientickern wie in diesem Beispiel nicht alphabetisch sortiert ist, kann es beim Zugriff auf die Kurs-Daten der Aktien und Returns Probleme mit der Reihenfolge geben, da die Download-Funktion von `yfinance` diese automatisch sortiert und somit nicht mehr der ursprünglichen Reihenfolge entspricht. Beim Berechnen der Portfoliowerte und -Returns ist die Reihenfolge allerdings wesentlich. Greift man den DataFrame direkt auf dem Array der Ticker ab, erzwingt man die ursprüngliche Reihenfolge.

In [ ]:
#vorgegebene Reihenfolge
print(tickers)

#automatische Sortierung
print(close_df.head())

#urspruengliche Reihenfolge
print(close_df[tickers].head())

calender_days = (close_df.index[-1] - close_df.index[0]).days
trading_days_per_year = 252
trading_days = len(close_df)

print("Kalendertage = %s, Handelstage = %s, Jahre (Handelstage) = %s, Jahre (Kalendertage) =%s" 
      % (calender_days, trading_days, trading_days / trading_days_per_year, calender_days / 365))




Wir nutzen dann später die Tages-Daten zur Schätzung der Kovarianz-Matrix und des Erwartungswertvektors der Returns, die wir zur Berechnung der erwarteten Portfolio-Returns sowie -Varianz benötigen. 

Wird in $t=0$ das Portfolio aus jeweils $a_j$ Stocks zum Preis $S_{j,0}$ zusammengesetzt ($j=1, \ldots,J$), gilt für den
jeweiligen Portfolioanteil der $j$-ten Aktie 

$$
w_j = \frac{a_j S_{j,0}}{P_0} \qquad \Leftrightarrow \qquad a_j = \frac{w_j P_0}{S_{j,0}}
$$ 

mit $\sum\limits_{j=1}^J w_j = 1$, wobei $P_0 = a_1 S_{1,0} + \ldots + a_J S_{J,0} = a^T S_0 = S_0^T a$ den investierte Gesamtbetrag beschreibt. Letztere Gleichung gilt für die Vektoren der Anzahl gekaufter Aktien $a^T = (a_1, \ldots, a_J)$ und den Vektor der Startkurse $S_0^T=(S_{1,0}, \ldots, S_{J,0})$ zur Investitionszeit in $t=0$.  


In [ ]:
print(tickers)

weights = np.array([0.1, 0.3, 0.4, 0.2])
print("Summe der Portfoliogewichte = %f" % weights.sum())

#erzwingen urspruengliche Reihenfolge der Aktien im tickers vektor
portfolio = close_df[tickers].copy()
print(portfolio.head())

#vgl. sortiert
print(close_df.head())

#type pandas dataframe
print("Type: %s" % type(portfolio))

startkapital = 1000
S0 = portfolio.iloc[0] #1. Zeile entspricht Startwerten
stueckzahl = weights / S0 *  startkapital
kaufpreis = sum(S0*stueckzahl)

print("kaufen in t=0 Stückzahl %s \n\n zum Preis %s \n\n für insgesamt  %.1f Dollar" % (stueckzahl, S0, kaufpreis) )

#alternative Berechnung als Skalarprodukt:
S0.dot(stueckzahl)



Damit können wir jetzt natürlich auch den Wert des Portfolios zu jedem späteren Zeitpunkt berechnen.
Wird das Portfolio bis zum Zeitpunkt $t>0$ nicht umgeschichtet, haben die Aktienkurse den Wert $S_t^T = (S_{1,t}, \ldots, S_{J,t})$ und somit das Portfolio den Wert 

$$
P_t = \sum\limits_{j=1}^n a_j S_{j,t} = a^T S_t = S_t^T a.
$$ 

Es bietet sich hierfür an die von Pandas bereitgestellten Matrix-Vektor-Operationen zu verwenden, denn die letzte Summe entspricht einfach dem Skalarprodukt zweier Vektoren[^7] und die Berechnung der Spalte aller Portfoliowerte über die Zeit entspricht entsprechend einer Matrix-Vektor-Multiplikation, die in Pandas mittels der `dot()` Funktion bereitgestellt wird ([Doku Pandas](https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.dot.html)). Wichtig ist allerdings, dass im DataFrame die Spalten in der gleichen Reihenfolge stehen, wie in den Vektoren - wir haben den DataFrame `portfolio` extra auf die Ticker-Reihenfolge angepasst, alternativ kann auch immer automatsichen mittels `portfolio[tickers]` explizit auf die Spalten der Aktien in der enstprechenden Reihenfolge zugegriffen werden.

[^7]: 
    Das Skalarprodukt zwischen dem Vektor $S_t = (S_{1,t}, \ldots, S_{J,t})^T$ der Aktienkurs zum Zeitpunkt $t$ und dem Vektor der Stückzahlen $a = (a_1, \ldots, a_J)^T$ wird wie folgt berechnet.

    $$
    <S_t,a> = S_t^T \cdot a = \sum\limits_{j=1}^J S_{j,t} a_j = P_t 
    $$

    Fassen wir nun alle Kurse der 4 Aktien (Spalten) über die Zeit als Matrix $S^T = \left\lbrace S_{j,t} \right\rbrace_{j=1,\ldots,J, t=0,1, \ldots, n}$ auf, dann ist $S^T a = (P_0, P_1, \ldots)^T$ gerade der Vektor aller Portfoliowerte.

In [ ]:
#Umwandeln in Numpy-Array, um einfacher zu rechnen
print(stueckzahl)
stueckzahl_np = stueckzahl.to_numpy()
print(stueckzahl_np)

portfolio['Portfolio'] = portfolio.dot(stueckzahl_np)
#portfolio['Portfolio'] = portfolio[tickers].dot(stueckzahl_np)

print(portfolio.head())

In [ ]:
portfolio.plot()

### Berechnung der Portfolio-Rendite

Für die Portfolio-Rendite, also den prozentualen Zuwachs bis zum Zeitpunkt $t$ des Portfolios gilt wegen 

\begin{align*} %eq-weigthed-ret
R^P_t &= \frac{P_t}{P_0}-1 = \sum\limits_{j=1}^J a_j \frac{S_{j,t}}{P_0} - 1 = \sum\limits_{j=1}^n a_j \frac{S_{j,0}}{P_0} \frac{S_{j,t}}{S_{j,0}} - 1 \\
&= \sum\limits_{j=1}^n w_j \left(\frac{S_{j,t}}{S_{j,0}} - 1 \right) = \sum\limits_{j=1}^n w_j R_{j,t} = R_t^T \cdot w = w^T \cdot R_t^T, 
\end{align*}

d. h. die Portfolio-Rendite ergibt sich als die gewichtete Summe der Aktien-Renditen $R_{j,t}=\frac{S_{j,t}}{S_{j,0}} - 1$ und kann bequem mittels Vektoren $R_t = (R_{1,t}, \ldots, R_{J,t})^T$ und Gewichtsvektor $w = (w_1, \ldots, w_J)^T$ auch wieder als Matrix-Vektor Produkt geschrieben werden. Für die Log-Returns gilt diese Beziehung zumindest näherungsweise, wie wir hier für unser Beispiel-Portfolio illustrieren.


In [ ]:
#daily returns / taegliche Renditen von t-1, t
print(portfolio.head())

tickers1 = tickers.copy()
tickers1.append("Portfolio")

renditen = portfolio.pct_change()
renditen["Days_Diff"] = renditen.index.to_series().diff().dt.days
renditen[tickers1].plot()
print(renditen.head())

Die Eigenschaft $R_t^P = w^T R_t$ gilt allerdings nur für die Renditen von 0 bis t und nicht für die täglichen, wie die folgende Rechnung zeigt:

In [ ]:
#Greifen explitzit nur die Spalten der Aktien-Ticker ab:
renditen["dot_version"] = renditen[tickers].dot(weights)
print(renditen.head())

#loeschen Spalte wieder (da falsch!)
renditen = renditen.drop(columns = ["dot_version"])




In [ ]:
#kumulierte Renditen von 0..t
renditen_kum = renditen.copy()

renditen_kum[tickers1]=(1+renditen_kum[tickers1]).cumprod()-1
renditen_kum["Days"] = renditen_kum["Days_Diff"].cumsum()

renditen_kum["dot_version"] = renditen_kum[tickers].dot(weights)
renditen_kum["check"] = renditen_kum["Portfolio"] - renditen_kum["dot_version"]
renditen_kum["Portfolio-Log-Return"] = np.log(renditen_kum.Portfolio+1)

#print(renditen_kum.tail())

print(renditen_kum[["Portfolio","dot_version","check"]].head())

norm_check_renditen = np.linalg.norm(renditen_kum["check"].dropna(), ord=2)  #euklid
##2-norm vs inf-norm
np.linalg.norm(renditen_kum["check"].dropna(), ord=2)  
np.linalg.norm(renditen_kum["check"].dropna(), ord=np.inf)  

ax = renditen_kum.plot(y=["Portfolio","dot_version","check","Portfolio-Log-Return"])
ax.lines[0].set_linestyle("--")
ax.lines[1].set_linestyle(":")
ax.lines[2].set_linestyle("-.")
ax.lines[3].set_linestyle("solid")
plt.show()
print("kumulierte Renditen: 2-Norm Fehler = %s (gerundet: %10f)" % (norm_check_renditen,np.round(norm_check_renditen, 10)))

Wir sehen dass die beiden Spalten 'Portfolio', bei dem die Zuwachsraten von 0 bis t direkt aus den Portfoliowerten, und die Spalte 'dot_version', bei dem die kumulierten Portfolio-Renditen als gewichtete Summe wie in Formel {eq}`eq-weigthed-ret` berechnet wurden bis auf minimale numerische Fehler (Spalte 'check' mit Norm nahe Null) tatsächlich übereinstimmen. 

In [ ]:
renditen_kum.plot(y=["check"])


Ein Plot der kumulierten Returns aller einzelnen Aktien sowie des Portfolios zeigt die Diversifikationseffekte recht deutlich, denn die Volatilität der Tesla-Aktie, in die 20% investiert wurde, wird deutlich ausgeglättet, obwohl alle Renditen einen positiven Zusammenhang aufweisen.


In [ ]:
renditen_kum[tickers1].plot()

Die Berechnung der Log-Returns des Portfolios läuft analog (aus Bequemlichkeit rechnen wir hier einfach die Renditen in Log-Returns nach Formel {eq}`rendite-vs-log-returns` um, allerdings kann man wie oben gezeigt auch direkt die Log-Returns mittels `diff()` Operator ausrechnen


In [ ]:
log_returns = renditen.copy()
log_returns[tickers1] = np.log(renditen[tickers1] + 1)
log_returns[tickers1].plot()
plt.show()


print(log_returns.head())



In [ ]:
log_returns2 = portfolio.copy()
log_returns2[tickers1] = np.log(log_returns2[tickers1]).diff()
print(log_returns2.head())


Überganzg von täglichen Returns zu kumulierten Returns:

In [ ]:
log_returns_kum = log_returns.copy()
log_returns_kum["Days"] = log_returns_kum["Days_Diff"].cumsum()
log_returns_kum[tickers1] = log_returns_kum[tickers1].cumsum()

log_returns_kum["dot_version"] = log_returns_kum[tickers].dot(weights)
log_returns_kum["check"] = log_returns_kum["Portfolio"] - log_returns_kum["dot_version"]
log_returns_kum["Portfolio-Rendite"] = np.exp(log_returns_kum.Portfolio) - 1



print(log_returns_kum[["Portfolio","dot_version","check"]].head())

norm_check_log_returns = np.linalg.norm(log_returns_kum["check"].dropna(), ord=2)  #euklid
##2-norm vs inf-norm
np.linalg.norm(log_returns_kum["check"].dropna(), ord=2)  
np.linalg.norm(log_returns_kum["check"].dropna(), ord=np.inf)  

ax = log_returns_kum.plot(y=["Portfolio","dot_version","check","Portfolio-Rendite"])
ax.lines[0].set_linestyle("--")
ax.lines[1].set_linestyle(":")
ax.lines[2].set_linestyle("-.")
ax.lines[3].set_linestyle("solid")
plt.show()
print("kumulierte Log-Returns: 2-Norm Fehler = %s (gerundet: %10f)" % (norm_check_log_returns,np.round(norm_check_log_returns, 10)))

#log_returns_kum.head()

In [ ]:
log_returns_kum.plot(y=["check"])

Wir sehen also, dass für die kumulierten Log-Returns des Portfolios zumindest näherungsweise $r_t^P \approx w^T \cdot r_t$ gilt. Die Graphiken zeigen, dass der Fehler überschaubar ist. 

### Zufalls-Modell

Wir haben im vorherigen AAbschnitt gesehen, dass für die Portfolio-Rendite $R^P_t = w^t R_t$ gilt und für die Log-Returns diese Beziehung in sehr guter Näherung gilt. Aus diesem Grund wird der zufällige Portfolio-Return häufig mittels 

$$
R^P_t = w^T R_t
$$(portfolio-ret) 

unabhängig von der tatsächlich verwendeten Return-Definition angesetzt, wobei der Vektor der Aktien-Returns bis zum Zeitpunkt t als Zufallsvariable modelliert wird. Die Porfolio-Theorie beschäftigt sich mit einer geeigneten Wahl des Gewichtsvektors unter verschiedenen Risiko-Kriterien. Im klassichen **Markowitz** Modell geht man davon aus, dass die zufällige Rendite $R_t^T = (R_{1,t},\ldots, R_{J,t}) \sim \mathcal{N}_J(\mu_t, \Sigma_t)$ aller Aktien einer multivariaten Normalverteilung genügt und daher durch die ersten beiden Momente $\mu_t = \mathbb{E}R_t$ und $\Sigma_t = \operatorname{cov}(R_t)$ vollständig das Zufallsverhalten charakterisieren. Für beliebig verteilte Zufallsvektoren reichen die ersten beiden Momente der Verteilung nicht. Wir haben oben gesehen, dass Log-Returns (zeitstetige Modelle) und die prozentualen Renditen (zeitdiskrete Modelle, arithmetische Returns) sich zwar leicht unterscheiden und aus mathematischer Sicht jeweils Vor- und Nachteile mitbringen. Während die Log-Returns aufgrund ihrer Additivität eher mit der Normalverteilungsannahme[^8] einhergehen, folgen die Renditen dann wegen Formel {eq}`rendite-vs-log-returns` einer Log-Normalverteilung.  

[^8]: Für die Log-Returns von 0 bis zum Zeitpunkt t gilt $r_{t} = \log{\left(\frac{S_t}{S_0}\right)} = \sum\limits_{i=1}^t r_{i-1,i}$, d. h. wenn wir die täglichen Log-Returns als iid (identisch und unabhängig verteilt) annehmen, so folgt aus dem zentralen Grenzwertsatz automatisch die Normalverteilung der Summe  $r_{t}$. Obige Auswertung hat gezeigt, dass die täglichen Returns zwar von einer Normalverteilung abweichen, aber dennoch einen glockenförmige Verteilung besitzen. 

Ein weiterer Vorteil der Log-Returns gegenüber den Renditen ist die einfachere Skalierbarkeit der ersten beiden Momente $\Sigma$ und $\mu$, so dass diese aus den vorhandenen Tages-Returns geschätzt werden können und dann wie in Abschnitt {ref}`annulized-ret`  beschrieben, einfach auf den Anlagezeitraum von 0 bis t skaliert werden können. Daher werden häufig die Log-Returns in der Finanzmathematik und insbesondere in der Portfolio-Theorie verwendet. Häufig unterstellt man für effiziente Finanzmärkte die Unkorreliertheit der Tages-Returns zwischen verschiedenen Handelstagen, wie wir das auch für die Skalierung der annualizierten Momente ausgenutzt haben, so dass alle relevanten und verfügbaren Informationen über die Aktiengesellschaften tatsächlich schon in den aktuellen Kursen eingepreist sind.

(portfolio-momente)=
### Portfolioanalyse: erwarteter Portfolio-Return und Portfolio-Varianz


Wegen Formel {eq}`portfolio-ret` können wir die erwartete Rendite  $\mathbb{E} R^P_t = \mu_t ^T w$ sowie die Portfolio-Varianz einfach mittels der ersten beiden Momente des Zufalls-Vektors $R_t^T = (R_{1,t}, \ldots, R_{J,t})$ der Aktien-Returns $\mu_t = \mathbb{E} R_t$ sowie $\Sigma_t = \operatorname(R_t) = \mathbb{E} \left( R_t - \mathbb{E} R_t \right) \left(R_t - \mathbb{E} R_t \right)^T$ ableiten

\begin{align*}
\mathbb{E} R_t^P &= \mathbb{E} \left( R_t^T \cdot w \right) = \left( \mathbb{E} R_t^T \right) \cdot w = \mu_t^T \cdot w \\
\operatorname{Var} (R_t^P) &= \mathbb{E} \left( \left( R_t^T \cdot w  - \mathbb{E}(R_t^T \cdot w) \right)^T \left( R_t^T \cdot w  - \mathbb{E}(R_t^T \cdot w) \right) \right)\\
&= w^T \left\lbrace \mathbb{E} \left( R_t - \mathbb{E} R_t \right) \left(R_t - \mathbb{E} R_t \right)^T \right\rbrace w\\
&= w^T \Sigma_t w
\end{align*}



Üblicherweise werden wie in {ref}`annulized-ret` beschrieben aus den Tages-Log-Returns mit Hilfe des arithmetsichen Mittels die erwarteten Tages-Returns bzw. Renditen geschätzt sowie deren Kovarianzmatrix berechnet und  anschließend durch Skalierung annualisiert. Verwendet man die Renditen nutzt den Zusammenhang ziwschen arithmetischen und geometrischen Mittel zur Annualisierung. Da wir streng genommen diese Annualisierung nur für die Log-Returns einfach berechnen können, kann man aber danach wieder zu den Renditen mittels Formel {eq}`rendite-vs-log-returns` übergehen. In der Praxis wird das nicht immer so konsequent unterschieden, aber wir haben ja gesehen, dass die Unterschiede zwischen Log-Returns und Renditen für kleinere Zeiträume nicht so deutlich sind, die folgenden Rechnungen zeigen dennoch die Probleme bei der Approximation auf. Aus diesem Grund wird tatsächlich bevorzugt mit den Log-Returns in der Portfolio-Theorie gearbeitet. 

<!--und daher der Approximationsfehler in Formel {eq}`eq-rendite-annualized-approx` nicht wesentlich ausfällt.-->

In [ ]:
mu_day = log_returns[tickers].mean()
mu_year = mu_day * trading_days_per_year

print(mu_year)

In [ ]:
mu_tilde_day = renditen[tickers].mean()
geo_mean_renditen = np.exp((np.log(renditen[tickers]+1)).mean()) - 1

print("mean daily R %s: \n " % mu_tilde_day)
print("geometric mean daily R %s: \n" % geo_mean_renditen)


In [ ]:
print("check: geo mean Rendite = exp(mean daily log)-1 = %s \n" % (np.exp(mu_day)-1) )
print("Daily log-returns %s: \n" % mu_day)

Wir sehen Abweichungen zwischen den geometrischen und arithmetischen Mittelwerten der täglichen Renditen bzw. Log-Returns. 
Außerdem sehen wir den den nichtlineare Zusammenhang zwischen mittleren Log-Returns und geometrischen Mittel der Renditen. Nun werden diese Mittel annualisiert. 

In [ ]:
mu_tilde_year  = (mu_tilde_day[tickers]+1) ** trading_days_per_year - 1

mu_tilde_year_approx1 = mu_tilde_day * trading_days_per_year 
mu_tilde_year_approx2 = np.exp(mu_year) -1

print("mu year (Log-Returns r) %s: \n " % mu_year)
print("mu_tilde year (Renditen R) %s: \n " % mu_tilde_year)
print("Approximation1 für Renditen: mu_tilde_year = mu_tilde * trading days_per_year %s\n " % (mu_tilde_year_approx1))
print("Approximation2 für Renditen: exp(mu_year) -1  %s: \n" % (mu_tilde_year_approx2))


 Die Auswirkungen auf die **erwartete** **jährliche** Portfoliorendite je nach Berechnungsart:

In [ ]:
print("erwartete annualisierte Portfoliorendite: \n"
"  %f (mu_tilde_year -- Rendite correct) \n"
"  %f (mu_year -- Log-Returns) \n"
"  %f (Approx1 Rendite) \n"
"  %f (Approx2 Rendite) \n" % 
      (mu_tilde_year.dot(weights),mu_year.dot(weights), mu_tilde_year_approx1.dot(weights), mu_tilde_year_approx2.dot(weights)))

Die 1. Approximation liefert bessere Ergebnisse für die Renditen, allerdings ist dieser Ansatz bei der Approximation der Kovarianz zu grob. 
<!--
daher werden wir aus Gründen der Einfachheit die simplere 1. Approximation für die Berechnung der Kovarianzmatrix der Jahres-Renditen $\tilde{\Sigma}_\text{annualized} \approx 252 \cdot \tilde{\Sigma}_\text{daily}$ verwenden. 
-->

Kovarianz- und Korrelationsmatzrix für Log-Returns

In [ ]:
Sigma_day = log_returns[tickers].cov()
Sigma_year = Sigma_day * trading_days_per_year 

print("Tages vs. Jahres-Kovarianz für Log-Returns")
print(Sigma_day)
print(Sigma_year)



Kovarianz- und Korrelationsmatzrix für Renditen

In [ ]:
Sigma_tilde_day = renditen[tickers].cov()

#Dummy zur simultanen Berechnung von (mu_tilde_i + 1)(mu_tilde_j + 1)
mu_tilde_dummy = np.outer(mu_tilde + 1, mu_tilde + 1)
#print(mu_tilde_dummy)

Sigma_tilde_year = (Sigma_tilde_day + mu_tilde_dummy)**trading_days_per_year - mu_tilde_dummy**trading_days_per_year

Sigma_tilde_year_approx1 = Sigma_tilde_day * trading_days_per_year

#Delta Method: 
exp_mu_year = np.exp(mu_year)
Sigma_tilde_year_approx2 =  (Sigma_year.dot(np.diag(exp_mu_year))).dot(np.diag(exp_mu_year))


#(Sigma_year.dot(weights)).dot(weights)

print("Tages vs. Jahres-Kovarianz für R")
print(Sigma_tilde_day)
print(Sigma_tilde_year)

print("Approx1 für R: Sigma \approx Sigma_tilde")
print(Sigma_tilde_year_approx1)

print("Approx2 für R: cov(R) = cov(e^r - 1) = cov(e^r) approx e^r cov(r) (e^r)^T (Delta-Methode für R_t = exp(r_t) - 1)")
print(Sigma_tilde_year_approx2)

Die deutlich bessere 2. Approximation basiert auf der <a href="https://en.wikipedia.org/wiki/Delta_method" target="_blank" rel="noopener noreferrer">Delta-Methode </a>.

Portvoliovarianz berechnet:

Für die Log-Returns

In [ ]:
P_log_var_year = (Sigma_year.dot(weights)).dot(weights)
print(P_log_var_year)

#alternative Berechnung mittels matmult
print(np.matmul(weights.transpose(), np.matmul(Sigma_year, weights)))

Für die Renditen

In [ ]:
P_var_year = (Sigma_tilde_year.dot(weights)).dot(weights)
print(P_var_year)








In [ ]:
P_var_year_approx1 = (Sigma_tilde_year_approx1.dot(weights)).dot(weights)
P_var_year_approx2 = (Sigma_tilde_year_approx2.dot(weights)).dot(weights)
print(P_var_year_approx1)
print(P_var_year_approx2)

In [ ]:
print("annualisierte Varianz der Portfolio-Rendite: \n"
"  %f (korrekt) \n"
"  %f (Approx1) \n"
"  %f (Approx2) \n" % 
      (P_var_year, P_var_year_approx1, P_var_year_approx2))